Text and code from: A matrix-free Discontinuous Galerkin method for the time dependent Maxwell equations in unbounded domains
Bernard Kapidani and Joachim Sch¨oberl, Archive X Feb 2020

In the following we present the script needed to simulate the
full 3D problem discussed in Section V, inclusive of PML. For
ease of presentation we leave out the interior penalty terms.
After importing the appropriate libraries, NetGen allows the
deﬁnition of geometry and meshing parameters of the domain
Ω through Constructive Solid Geometry (CSG) instructions,
starting from the background cuboid with unit length sides:

In [26]:
from ngsolve import *
from netgen.csg import *
from netgen import gui
#from ngsolve.webgui import Draw
SetHeapSize = 10*100*1000
# half-side length of the domain
xi = 0.5
yi = 0.5
zi = 0.5
xo = 0.6
yo = 0.6
zo = 0.6
geo = CSGeometry()
omega = (OrthoBrick(Pnt(-xi,-yi,-zi),Pnt(xi,yi,zi))) #original domain

optfile ./ng.opt does not exist - using default values
togl-version : 2
OCC module loaded
loading ngsolve library
NGSolve-6.2.2402
Using Lapack
Including sparse direct solver Pardiso
Running parallel using 8 thread(s)


All the other cuboids (“Orthobrick”) pertaining to the PML
can be defined in similar fashion. Finally, only the domains
which actually need to be meshed are added to the “geo”
object and the graphical user interface (GUI) is asked to show
the mesh via a “Draw” command

In [27]:
xpml = (OrthoBrick(Pnt(-xo,-yi,-zi),Pnt(xo,yi,zi))-omega).mat("xpml")
ypml = (OrthoBrick(Pnt(-xi,-yo,-zi),Pnt(xi,yo,zi))-omega).mat("ypml")
zpml = (OrthoBrick(Pnt(-xi,-yi,-zo),Pnt(xi,yi,zo))-omega).mat("zpml")
xypml = (OrthoBrick(Pnt(-xo,-yo,-zi),Pnt(xo,yo,zi))-omega-xpml-ypml).mat("xypml")
xzpml = (OrthoBrick(Pnt(-xo,-yi,-zo),Pnt(xo,yi,zo))-omega-xpml-zpml).mat("xzpml")
yzpml = (OrthoBrick(Pnt(-xi,-yo,-zo),Pnt(xi,yo,zo))-omega-ypml-zpml).mat("yzpml")
all_other_pml = xpml+ypml+zpml+xypml+xzpml+yzpml+omega
xyzpml = (OrthoBrick(Pnt(-xo,-yo,-zo),Pnt(xo,yo,zo))-all_other_pml).mat("xyzpml")
hole = (Sphere(Pnt(0,0,0),0.1)).bc("incidentfield")
omega = (omega-hole).mat("air") #new air filled domain
geo.Add(omega)
geo.Add(xpml)
geo.Add(ypml)
geo.Add(zpml)
geo.Add(xypml)
geo.Add(xzpml)
geo.Add(yzpml)
geo.Add(xyzpml)
mesh = Mesh(geo.GenerateMesh(maxh=0.1)) # maxh sets max mesh-size
Draw(mesh)

 Start Findpoints
 Analyze spec points
 Find edges
 Start Findpoints
 Analyze spec points
 Find edges
 Start Findpoints
 Analyze spec points
 Find edges
 Surface 1 / 49
 Optimize Surface
 Surface 2 / 49
 Optimize Surface
 Surface 3 / 49
 Optimize Surface
 Surface 4 / 49
 Optimize Surface
 Surface 5 / 49
 Optimize Surface
 Surface 6 / 49
 Optimize Surface
 Surface 7 / 49
 Optimize Surface
 Surface 8 / 49
 Optimize Surface
 Surface 9 / 49
 Optimize Surface
 Surface 10 / 49
 Optimize Surface
 Surface 11 / 49
 Optimize Surface
 Surface 12 / 49
 Optimize Surface
 Surface 13 / 49
 Optimize Surface
 Surface 14 / 49
 Optimize Surface
 Surface 15 / 49
 Optimize Surface
 Surface 16 / 49
 Optimize Surface
 Surface 17 / 49
 Optimize Surface
 Surface 18 / 49
 Optimize Surface
 Surface 19 / 49
 Optimize Surface
 Surface 20 / 49
 Optimize Surface
 Surface 21 / 49
 Optimize Surface
 Surface 22 / 49
 Optimize Surface
 Surface 23 / 49
 Optimize Surface
 Surface 24 / 49
 Optimize Surface
 Surface 25 / 49

The function “ CoefﬁcientFunction ” allows the piecewise-
smooth deﬁnition of scalar, vector and matrix valued functions
on Ω or ∂Ω. This is useful, for example, in deﬁning the
standard material tensors, which are 3 × 3 matrices. We deﬁne
also additional useful parameters in the simulation and the
special function “n”, which is the normal unit vector on each
ﬁnite element boundary, and it is always outwards pointing.

In [28]:
epsr = CoefficientFunction( (1, 0, 0, 0, 1, 0, 0, 0, 1), dims=(3,3))
mur = CoefficientFunction( (1, 0, 0, 0, 1, 0, 0, 0, 1), dims=(3,3))
mu0 = 1
eps0 = 1
n = specialcf.normal(mesh.dim)

The additional fictitious material tensors η(r), ξ(r) required
for the PML are also defined piecewise through dictionaries:

In [29]:
sig = 5 # sig=0 => no pml
eta = {}
xi = {}
eta["air"] = CoefficientFunction((0,0,0,0,0,0,0,0,0),dims=(3,3))
eta["xpml"] = CoefficientFunction((-sig,0,0,0,sig,0,0,0,sig),dims=(3,3))
eta["ypml"] = CoefficientFunction((sig,0,0,0,-sig,0,0,0,sig),dims=(3,3))
eta["zpml"] = CoefficientFunction((sig,0,0,0,sig,0,0,0,-sig),dims=(3,3))
eta["xypml"] = CoefficientFunction((0,0,0,0,0,0,0,0,2*sig),dims=(3,3))
eta["xzpml"] = CoefficientFunction((0,0,0,0,2*sig,0,0,0,0),dims=(3,3))
eta["yzpml"] = CoefficientFunction((2*sig,0,0,0,0,0,0,0,0),dims=(3,3))
eta["xyzpml"] = CoefficientFunction((sig,0,0,0,sig,0,0,0,sig),dims=(3,3))
xi["air"] = CoefficientFunction((0,0,0,0,0,0,0,0,0),dims=(3,3))
xi["xpml"] = CoefficientFunction((sig**2,0,0,0,0,0,0,0,0 ),dims=(3,3))
xi["ypml"] = CoefficientFunction((0,0,0,0,sig**2,0,0,0,0 ),dims=(3,3))
xi["zpml"] = CoefficientFunction((0,0,0,0,0,0,0,0,sig**2),dims=(3,3))
xi["xypml"] = CoefficientFunction((0,0,0,0,0,0,0,0,sig**2),dims=(3,3))
xi["xzpml"] = CoefficientFunction((0,0,0,0,sig**2,0,0,0,0),dims=(3,3))
xi["yzpml"] = CoefficientFunction((sig**2,0,0,0,0,0,0,0,0),dims=(3,3))
xi["xyzpml"] = CoefficientFunction((0,0,0,0,0,0,0,0,0),dims=(3,3))
eta = CoefficientFunction([eta[mat] for mat in mesh.GetMaterials()])
xi = CoefficientFunction([xi[mat] for mat in mesh.GetMaterials()])

The finite element spaces are then defined, for fields e, h and
auxiliary unknowns p, q. The keyword argument “ covariant ”
is fundamental, since it specifies that, even if the spaces
are fully discontinuous (“VectorL2”), they are mapped from
reference to physical element with the appropriate transforma-
tion. Keyword “ all dofs together ” forces DoFs pertaining to
each element to be adjacent in the global vector. Unknowns
are then grouped together into a Cartesian product space for
convenience, while all their the DoFs (stored in “ solution ”)
are initially set to zero and plotted in the GUI:

In [30]:
degree = 6
fes_e = VectorL2(mesh, order=degree+1,covariant=True, all_dofs_together=True)
fes_h = VectorL2(mesh, order=degree, covariant=True, all_dofs_together=True)
fes_p = VectorL2(mesh, order=degree+1,covariant=True, all_dofs_together=True)
fes_q = VectorL2(mesh, order=degree, covariant=True, all_dofs_together=True)
fes = FESpace( [fes_e,fes_h,fes_p,fes_q] )
edofs = fes.Range(0)
hdofs = fes.Range(1)
pdofs = fes.Range(2)
qdofs = fes.Range(3)
sol = GridFunction(fes)
sol.components[0].vec[:] = 0
sol.components[1].vec[:] = 0
sol.components[2].vec[:] = 0
sol.components[3].vec[:] = 0

To let operators act on the global vector of DoFs and on the
spaces for single unknowns without creating too many copy
of involved objects, we deﬁne embedding operators, which
amount to diagonal, positive-semideﬁnite matrices (containing
only zeros and ones), acting on the DoFs vector. Operator
composition is achieved through the “@” token.

In [31]:
emb_e = Embedding(fes.ndof, fes.Range(0))
emb_h = Embedding(fes.ndof, fes.Range(1))
emb_p = Embedding(fes.ndof, fes.Range(2))
emb_q = Embedding(fes.ndof, fes.Range(3))

Thus, after computing the all needed mass matrices (including
necessary damping terms), we can embed them in operators
acting on the global solution vector:

In [32]:
tau = 0.001 #time step size
alpha = 0.5*sig*tau
beta = 1/(1+alpha)
gamma = (1-alpha)*beta
tpar = Parameter(0)
massmate_eta = fes_e.Mass(eps0*(epsr-0.5*tau*eta*epsr))
massmath_eta = fes_h.Mass(mu0*(mur-0.5*tau*eta*mur))
massmate_xi = fes_e.Mass(eps0*(eta*epsr))
massmath_xi = fes_h.Mass(mu0*(eta*mur))
invmasse_eta = fes_e.Mass(eps0*(epsr+0.5*tau*eta*epsr)).Inverse()
invmassh_eta = fes_h.Mass(mu0*(mur+0.5*tau*eta*mur)).Inverse()
mate_eta = emb_e @ massmate_eta @ emb_e.T
math_eta = emb_h @ massmath_eta @ emb_h.T
inve_eta = emb_e @ invmasse_eta @ emb_e.T
invh_eta = emb_h @ invmassh_eta @ emb_h.T
mate_xi = emb_p @ massmate_xi @ emb_e.T
math_xi = emb_q @ massmath_xi @ emb_h.T

A Python function defines the main loop of the script, where
time-stepping is actually performed: the operators for the
discrete curl are still abstract and will be defined in a later
code-block.

In [33]:
def Run(CE, CH, t0 = 0, tend = 1, tau = 1e-3):
    t = 0
    dummy = sol.vec.CreateVector()
    with TaskManager():
        print("t = ",t)
        tpar = t
        while t < (tend-t0) - tau/2:
            t += tau
            # E, H solution update
            dummy.vec.data = inve_eta @ mate_eta*sol.vec + tau*inve_eta @ CE*sol.vec
            sol.vec[edofs] = dummy.vec[edofs]
            dummy.vec.data = invh_eta @ math_eta*sol.vec + tau*invh_eta @ CH*sol.vec
            sol.vec[hdofs] = dummy.vec[hdofs]
            Redraw(nonblocking=True)
            # auxiliary variables update
            dummy.vec.data = gamma*emb_p @ emb_p.T*sol.vec + beta*mate_xi*sol.vec
            sol.vec[pdofs] = dummy.vec[pdofs]
            dummy.vec.data = gamma*emb_q @ emb_q.T*sol.vec + beta*math_xi*sol.vec
            sol.vec[qdofs] = dummy.vec[qdofs]

The incident field can be then enforced, via a python dic-
tionary, on the appropriate boundary surfaces in the mesh.
Namely the one labelled above with the “ incidentfield ”
boundary condition.

In [34]:
Einc = {}
Einc["default"] = CoefficientFunction( (0,0,0) )
Einc["incidentfield"] = CoefficientFunction( (exp(-((tpar-300*tau)/(10*tau))**2),0,0) )
Einc = CoefficientFunction([Einc[bb] for bb in (mesh.GetBoundaries())])

All the terms described in Section III for the curl operator are
given below in terms of bilinear-form integrators, where the
syntax is inherited from the language of differential forms and
the “element boudary” keyword denotes integration on ∂T ,
for each element T ∈ TΩ. Another crucial keyword argument
introduced in the following code snippet is “geom free”: this
flag, when set to true, signals to the interpreter that the
associated bilinear form is independent from the geometry of
any particular finite element, which prompts the library to opti-
mize integration, by building a single local reference operator
(matrix). A caveat must be mentioned: the responsibility of
checking the mathematics to ensure that this is really the case
falls on the user.

In [35]:
h = fes_h.TestFunction()
E = fes_e.TrialFunction()

C_el = BilinearForm(trialspace=fes_e, testspace=fes_h, geom_free = True)
C_el += -curl(E)*h*dx
C_el.Assemble()

C_tr = BilinearForm(trialspace=fes_e, testspace=fes_h, geom_free = True)
C_tr += 0.5*Cross(E.Other(bnd=2*Einc+E)-E,n)*h*dx(element_boundary=True)
C_tr.Assemble()

C_EH = emb_h @ (C_el.mat + Ctr.mat) @ emb_e.T
C_e = C_EH.T - (emb_e @ emb_p.T)
C_h = -C_EH + (emb_h @ emb_q.T)

NgException: FacetBilinearFormIntegrator can not assemble volumetric element matrices!

We are finally ready to run the simulation: we tell the GUI to
plot the initial (zeroed) solutions for the electro-magnetic field
and we call the “Run” function with the appropriate arguments.
The “Redraw” calls inside the loop, will update the plots at
each time step.

In [25]:
Draw(sol.components[1], mesh, "H")
Draw(sol.components[0], mesh, "E")
Run(C_e, C_h,0,1.2,tau)

NgException: GridFunctionCoefficientFunction: SIMD: don't know how I shall evaluate